# Базовое использование RAG Chat API

Простой пример работы с API для получения ответов на вопросы.



In [1]:
import requests
import json
import time
from IPython.display import display, Markdown, HTML
import pandas as pd

API_URL = "http://localhost:9004"

question = "Что такое донорство крови?"
print(f"❓ Вопрос: {question}\n")

response = requests.post(
    f"{API_URL}/api/chat/stream",
    json={
        "message": question,
        "conversation_id": None
    },
    stream=True
)

if response.status_code != 200:
    print(f"❌ Ошибка: {response.status_code}")
    print(response.text)
else:
    full_answer = ""
    conversation_id = None
    metadata = {}
    status_messages = []
    start_time = time.time()
    
    for line in response.iter_lines():
        if line:
            line_str = line.decode('utf-8')
            if line_str.startswith('data: '):
                try:
                    data = json.loads(line_str[6:])
                    if data.get('type') == 'start':
                        conversation_id = data.get('conversation_id')
                    elif data.get('type') == 'token':
                        full_answer += data.get('content', '')
                        print(data.get('content', ''), end='', flush=True)
                    elif data.get('type') == 'end':
                        metadata = data.get('metadata', {})
                        break
                    elif data.get('type') == 'status':
                        status_msg = f"[{data.get('status', 'info')}] {data.get('message', '')}"
                        status_messages.append(status_msg)
                        print(f"\n{status_msg}")
                except json.JSONDecodeError as e:
                    print(f"\n⚠️ Ошибка парсинга JSON: {e}")
    
    elapsed_time = time.time() - start_time
    
    print("\n\n" + "="*60)
    print("📊 Результаты запроса:")
    print("="*60)
    
    if conversation_id:
        print(f"🆔 Conversation ID: {conversation_id}")
    
    if metadata:
        print(f"⏱️ Время поиска: {metadata.get('search_time', 0):.2f}с")
        print(f"⏱️ Время генерации: {metadata.get('generation_time', 0):.2f}с")
        print(f"📄 Найдено документов: {metadata.get('documents_found', 0)}")
    
    print(f"⏱️ Общее время: {elapsed_time:.2f}с")
    print(f"📝 Длина ответа: {len(full_answer)} символов")
    
    print("\n" + "="*60)
    print("💬 Полный ответ:")
    print("="*60)
    display(Markdown(full_answer))



❓ Вопрос: Что такое донорство крови?


[searching] Поиск информации в базе знаний...

[processing] Нашла релевантные материалы. Извлекаю ключевые факты и проверяю даты из подтверждённых источников...

[generating] Генерация ответа...
Донорство крови — это добровольная сдача крови или её компонентов (цельной крови, плазмы, тромбоцитов, аферезных эритроцитов) в медицинские учреждения, где она используется для переливания пациентам, нуждающимся в крови.  

**Ключевые моменты:**

1. **Кто может стать донором**  
   - Возраст ≥ 18 лет (для донорства костного мозга – 18–45 лет).  
   - Вес ≥ 50 кг, нормальный гемоглобин (проверяется экспресс‑анализом в день донации).  
   - Отсутствие противопоказаний (болезни, лекарства, недавние операции, инфекционные заболевания и т.д.).  
   - Наличие паспорта и СНИЛС (или временного удостоверения личности).

2. **Частота донаций**  
   - Цельная кровь и плазма — не более 3 раз в год, интервал ≥ 56 дней.  
   - Тромбоциты — не более 1 раз в 7 дней.  
   

Донорство крови — это добровольная сдача крови или её компонентов (цельной крови, плазмы, тромбоцитов, аферезных эритроцитов) в медицинские учреждения, где она используется для переливания пациентам, нуждающимся в крови.  

**Ключевые моменты:**

1. **Кто может стать донором**  
   - Возраст ≥ 18 лет (для донорства костного мозга – 18–45 лет).  
   - Вес ≥ 50 кг, нормальный гемоглобин (проверяется экспресс‑анализом в день донации).  
   - Отсутствие противопоказаний (болезни, лекарства, недавние операции, инфекционные заболевания и т.д.).  
   - Наличие паспорта и СНИЛС (или временного удостоверения личности).

2. **Частота донаций**  
   - Цельная кровь и плазма — не более 3 раз в год, интервал ≥ 56 дней.  
   - Тромбоциты — не более 1 раз в 7 дней.  
   - Аферез эритроцитов — не более 2 раз в год, интервал ≥ 14 дней.  
   - После сдачи плазмы можно сдавать цельную кровь через 28 дней и наоборот.

3. **Подготовка к сдаче**  
   - За 48 ч — не пить алкоголь, за 72 ч — не принимать аспирин/анальгетики.  
   - За час до процедуры воздержаться от курения.  
   - Избегать жирной, жареной, копченой пищи, молочных продуктов, бананов, авокадо, свеклы.  
   - Пить воду, соки, компоты, чай, есть хлеб, сухари, отварные крупы, овощи и фрукты (без запрещённых).  
   - Завтрак обязателен, ужин накануне легкий.

4. **Код донации**  
   - Выдается только в регистратуре учреждения, подключённого к АИСТ/ЕИБД.  
   - Вводится в МП «Служба крови» или в личный кабинет на https://yadonor.ru/ для просмотра истории и учета.  
   - Не выдаётся по СМС, только в регистратуре.

5. **После сдачи**  
   - 10–15 минут в положении лежа, затем сидеть, не поднимать тяжести.  
   - Не снимать повязку до 3–4 ч.  
   - Пить минимум 2 л жидкости в течение 48 ч.  
   - Избегать алкоголя и тяжёлых физических нагрузок в первый день.

6. **Контакты**  
   - Для записи, уточнения графика работы и вопросов по донорству можно воспользоваться порталом https://yadonor.ru/ или позвонить по бесплатному номеру 8-800-333-33-43.  

Донорство крови — важный вклад в общественное здоровье, позволяющий спасать жизни пациентов, нуждающихся в переливании.

## Получение полного ответа



In [2]:
from IPython.display import display, Markdown
import pandas as pd

def get_answer(question: str, api_url: str = API_URL, show_progress: bool = True):
    response = requests.post(
        f"{api_url}/api/chat/stream",
        json={"message": question},
        stream=True
    )
    
    if response.status_code != 200:
        return None, None, None, f"Ошибка: {response.status_code}"
    
    full_answer = ""
    conversation_id = None
    metadata = {}
    start_time = time.time()
    
    for line in response.iter_lines():
        if line:
            line_str = line.decode('utf-8')
            if line_str.startswith('data: '):
                try:
                    data = json.loads(line_str[6:])
                    if data.get('type') == 'start':
                        conversation_id = data.get('conversation_id')
                    elif data.get('type') == 'token':
                        full_answer += data.get('content', '')
                        if show_progress:
                            print(data.get('content', ''), end='', flush=True)
                    elif data.get('type') == 'end':
                        metadata = data.get('metadata', {})
                        break
                    elif data.get('type') == 'status' and show_progress:
                        print(f"\n[{data.get('status', 'info')}] {data.get('message', '')}")
                except json.JSONDecodeError:
                    continue
    
    elapsed_time = time.time() - start_time
    return full_answer, conversation_id, metadata, elapsed_time

question = "Какие есть противопоказания для донорства?"
print(f"❓ Вопрос: {question}\n")

answer, conv_id, meta, elapsed = get_answer(question)

if answer:
    print("\n\n" + "="*60)
    
    results_df = pd.DataFrame([{
        'Параметр': 'Conversation ID',
        'Значение': conv_id
    }, {
        'Параметр': 'Время поиска',
        'Значение': f"{meta.get('search_time', 0):.2f}с" if meta else "N/A"
    }, {
        'Параметр': 'Время генерации',
        'Значение': f"{meta.get('generation_time', 0):.2f}с" if meta else "N/A"
    }, {
        'Параметр': 'Найдено документов',
        'Значение': meta.get('documents_found', 0) if meta else "N/A"
    }, {
        'Параметр': 'Общее время',
        'Значение': f"{elapsed:.2f}с"
    }, {
        'Параметр': 'Длина ответа',
        'Значение': f"{len(answer)} символов"
    }])
    
    display(results_df)
    
    print("\n" + "="*60)
    print("💬 Ответ:")
    print("="*60)
    display(Markdown(answer))
else:
    print(f"❌ {conv_id}")



❓ Вопрос: Какие есть противопоказания для донорства?


[searching] Поиск информации в базе знаний...

[processing] Нашла релевантные материалы. Извлекаю ключевые факты и проверяю даты из подтверждённых источников...

[generating] Генерация ответа...
**Постоянные медицинские противопоказания**  
(согласно Приказу Минздрава РФ № 1166н от 28.10.2020)

| Группа заболеваний | Примерные варианты |
|--------------------|--------------------|
| Инфекционные заболевания | ВИЧ‑инфекция, сифилис, вирусные гепатиты B, C, D, E, туберкулез, острые вирусные инфекции (грипп, ОРВИ) |
| Онкологические заболевания | Злокачественные новообразования, химиотерапия, лучевая терапия |
| Болезни крови | Анемия, гемофилия, лейкемия, лимфома, тромбоцитопения |
| Хронические заболевания печени | Цирроз, хронический гепатит |
| Хронические заболевания почек | Печеночная недостаточность, хроническая почечная недостаточность |
| Сердечно‑сосудистые заболевания | Пороки сердца, хроническая сердечная недостаточность, 

Параметр          Значение
0     Conversation ID  9a6da58c2e85054d
1        Время поиска             0.13с
2     Время генерации             7.85с
3  Найдено документов                20
4         Общее время             8.17с
5        Длина ответа     2567 символов


💬 Ответ:


**Постоянные медицинские противопоказания**  
(согласно Приказу Минздрава РФ № 1166н от 28.10.2020)

| Группа заболеваний | Примерные варианты |
|--------------------|--------------------|
| Инфекционные заболевания | ВИЧ‑инфекция, сифилис, вирусные гепатиты B, C, D, E, туберкулез, острые вирусные инфекции (грипп, ОРВИ) |
| Онкологические заболевания | Злокачественные новообразования, химиотерапия, лучевая терапия |
| Болезни крови | Анемия, гемофилия, лейкемия, лимфома, тромбоцитопения |
| Хронические заболевания печени | Цирроз, хронический гепатит |
| Хронические заболевания почек | Печеночная недостаточность, хроническая почечная недостаточность |
| Сердечно‑сосудистые заболевания | Пороки сердца, хроническая сердечная недостаточность, артериальная гипертензия, инфаркт миокарда |
| Психические расстройства | Серьёзные психические заболевания, которые могут повлиять на безопасность донации |
| Другие | Тяжёлые аллергии, хронические воспалительные заболевания, тяжелые травмы |

**Временные медицинские противопоказания**  
(срок отвода от донорства зависит от конкретного случая)

| Противопоказание | Срок отвода |
|------------------|-------------|
| Татуировка, пирсинг, иглоукалывание | 120 календарных дней |
| Операция (в том числе аппендицит) | 120 календарных дней |
| Острая инфекция (грипп, ОРВИ) | 30 календарных дней |
| Беременность и лактация | 1 год после родов, 90 дней после окончания лактации |
| Вакцинация (COVID‑19, другие) | 30 календарных дней после второй дозы |
| Лечение антибиотиками, анальгетиками (аспирин) | 72 часа после приёма |
| Острая травма, перелом | 30 календарных дней |
| Период менструации | 5 дней после окончания менструации (рекомендовано) |

**Физические и социальные критерии**

| Критерий | Требование |
|----------|------------|
| Возраст | ≥ 18 лет (для донорства костного мозга – 18–55 лет) |
| Вес | ≥ 50 кг |
| Гемоглобин | Проверяется экспресс‑анализом в день донации (для мужчин ≥ 140 г/л, для женщин ≥ 120 г/л) |
| Паспорт и СНИЛС | Обязательны (или временное удостоверение личности) |

**Важно**  
- При наличии любого из перечисленных противопоказаний необходимо обратиться к врачу‑трансфузиологу для уточнения индивидуального статуса.  
- Если вы считаете, что у вас есть заболевание, не входящее в список, но которое может повлиять на безопасность донации, врач решит вопрос о допуске на основе клинической оценки.

Для записи на донацию, уточнения графика работы и вопросов по донорству можно воспользоваться порталом https://yadonor.ru/ или позвонить по бесплатному номеру 8-800-333-33-43.